In [1]:
import numpy as np
import pandas
import pm4py
from matplotlib import pyplot as plt
from sklearn.mixture import GaussianMixture
import scipy.stats as stats
import ot
import os
from tqdm import tqdm
import collections
import matplotlib.dates as md
import importlib
import pickle
import random
import math
import CRPS.CRPS as pscore
import datetime

pandas.set_option('display.max_columns', None)
#pandas.set_option('display.max_rows', None)


import sys
sys.path.append('../../TaskExecutionTimeMining/')
from drbart_parser import *
from event_log_transformer import *

#sys.path.append('../../Evaluation')
sys.path.append('../../Evaluation/')
from normal_evaluation.drbart_evaluation import *

In [2]:
#model_name = 'bpic_2017_all_2'
model_name = 'bpic_2017_all'

log_name = 'test'
with open('../transformed_event_logs/BPIC_2017_all_'+log_name+'.pickle', 'rb') as f:
    test_event_log = pickle.load(f)

test_event_log['case:concept:name'] = test_event_log['case:concept:name'].astype(str)
known_resources = ['User_1','User_10','User_100','User_101','User_102','User_103','User_104','User_105','User_106','User_107','User_108','User_109','User_11','User_110','User_111','User_112','User_113','User_114','User_115','User_116','User_117','User_118','User_119','User_12','User_120','User_121','User_122','User_123','User_124','User_125','User_126','User_127','User_128','User_129','User_13','User_130','User_131','User_132','User_133','User_134','User_135','User_136','User_137','User_138','User_139','User_14','User_140','User_141','User_142','User_143','User_144','User_145','User_146','User_147','User_148','User_149','User_15','User_16','User_17','User_18','User_19','User_2','User_20','User_21','User_22','User_23','User_24','User_25','User_26','User_27','User_28','User_29','User_3','User_30','User_31','User_32','User_33','User_34','User_35','User_36','User_37','User_38','User_39','User_4','User_40','User_41','User_42','User_43','User_44','User_45','User_46','User_47','User_48','User_49','User_5','User_50','User_51','User_52','User_53','User_54','User_55','User_56','User_57','User_58','User_59','User_6','User_60','User_61','User_62','User_63','User_64','User_65','User_66','User_67','User_68','User_69','User_7','User_70','User_71','User_72','User_73','User_74','User_75','User_76','User_77','User_78','User_79','User_8','User_80','User_81','User_82','User_83','User_84','User_85','User_86','User_87','User_88','User_89','User_9','User_90','User_91','User_92','User_93','User_94','User_95','User_96','User_97','User_98','User_99']
known_activities = ['W_Assess potential fraud__ate_abort','W_Assess potential fraud__complete','W_Assess potential fraud__resume','W_Assess potential fraud__schedule','W_Assess potential fraud__start','W_Assess potential fraud__suspend','W_Assess potential fraud__withdraw','W_Call after offers__ate_abort','W_Call after offers__complete','W_Call after offers__resume','W_Call after offers__schedule','W_Call after offers__start','W_Call after offers__suspend','W_Call after offers__withdraw','W_Call incomplete files__ate_abort','W_Call incomplete files__complete','W_Call incomplete files__resume','W_Call incomplete files__schedule','W_Call incomplete files__start','W_Call incomplete files__suspend','W_Complete application__ate_abort','W_Complete application__complete','W_Complete application__resume','W_Complete application__schedule','W_Complete application__start','W_Complete application__suspend','W_Handle leads__complete','W_Handle leads__resume','W_Handle leads__schedule','W_Handle leads__start','W_Handle leads__suspend','W_Handle leads__withdraw','W_Shortened completion __resume','W_Shortened completion __schedule','W_Shortened completion __start','W_Shortened completion __suspend','W_Validate application__ate_abort','W_Validate application__complete','W_Validate application__resume','W_Validate application__schedule','W_Validate application__start','W_Validate application__suspend']

/tmp/ipykernel_2163797/2121463303.py:6: DeprecationWarning: numpy.core.numeric is deprecated and has been renamed to numpy._core.numeric. The numpy._core namespace contains private NumPy internals and its use is discouraged, as NumPy internals can change without warning in any release. In practice, most real-world usage of numpy.core is to access functionality in the public NumPy API. If that is the case, use the public NumPy API. If not, you are using NumPy internals. If you would still like to access an internal attribute, use numpy._core.numeric._frombuffer.
  test_event_log = pickle.load(f)


In [3]:
test_event_log

Action_start org:resource_start                       concept:name  \
0           Created           User_112   W_Validate application__schedule   
3          Released            User_30   W_Call incomplete files__suspend   
9          Released             User_5   W_Call incomplete files__suspend   
12         Obtained            User_29     W_Call incomplete files__start   
14         Obtained            User_96         W_Call after offers__start   
...             ...                ...                                ...   
619746      Created           User_109  W_Call incomplete files__schedule   
619760      Created             User_1           W_Handle leads__schedule   
619768     Obtained           User_131      W_Validate application__start   
619771      Created             User_4   W_Complete application__schedule   
619781     Obtained             User_5        W_Call after offers__resume   

       EventOrigin_start        EventID_start lifecycle:transition_start  \
0               Workflow   Workitem_100000116                   schedule   
3               Workflow  Workitem_1000014801                    suspend   
9               Workflow  Workitem_1000028973                    suspend   
12              Workflow  Workitem_1000031049                      start   
14              Workflow  Workitem_1000036756                      start   
...                  ...                  ...                        ...   
619746          Workflow   Workitem_999833898                   schedule   
619760          Workflow   Workitem_999873530                   schedule   
619768          Workflow   Workitem_999916513                      start   
619771          Workflow   Workitem_999936192                   schedule   
619781          Workflow   Workitem_999993228                     resume   

                   time:timestamp_start     case:LoanGoal_start  \
0      2016-03-02 13:25:52.388000+00:00        Home improvement   
3      2016-11-30 16:55:49.483000+00:00           Not speficied   
9      2016-03-09 11:02:30.451000+00:00  Existing loan takeover   
12     2016-10-03 13:50:01.644000+00:00                     Car   
14     2016-11-22 16:55:50.288000+00:00  Existing loan takeover   
...                                 ...                     ...   
619746 2016-03-08 10:04:34.454000+00:00     Remaining debt home   
619760 2016-06-23 10:18:19.812000+00:00                     Car   
619768 2016-10-18 07:50:28.148000+00:00        Home improvement   
619771 2016-04-28 17:34:53.020000+00:00                     Car   
619781 2016-06-20 12:37:57.929000+00:00  Existing loan takeover   

       case:ApplicationType_start       case:concept:name  \
0                     Limit raise  Application_1650545424   
3                      New credit   Application_655052891   
9                      New credit   Application_712301423   
12                    Limit raise   Application_237359086   
14                     New credit   Application_729141109   
...                           ...                     ...   
619746                 New credit  Application_1664730949   
619760                 New credit  Application_1467321049   
619768                 New credit   Application_480209137   
619771                 New credit   Application_570083989   
619781                 New credit  Application_1107879965   

        case:RequestedAmount_start  FirstWithdrawalAmount_start  \
0                          40000.0                          0.0   
3                           7000.0                          0.0   
9                          20000.0                          0.0   
12                         15500.0                          0.0   
14                         11000.0                          0.0   
...                            ...                          ...   
619746                         0.0                          0.0   
619760                      6000.0                          0.0   
619768                     2

In [3]:
N = 1000
n_processes = 12

import conduct_evaluation
get_pscores = lambda likelihoods : [pscore(likelihoods[1][i], likelihoods[2][k][3]).compute()[0] for i, k in enumerate(list(likelihoods[0].keys()))]

likelihoods_A = None
likelihoods_R = None
likelihoods_R_A = None
likelihoods_R_A_S = None
likelihoods_R_A_S_AC = None
likelihoods_R_A_S_RC = None
likelihoods_R_A_S_RC_AC = None
likelihoods_R_A_S_RC_AC_V = None
likelihoods_R_A_S_D = None
likelihoods_R_A_S_D_RC_AC = None

In [5]:
#needs strict_parser=False
#otherwise: KeyError: 'W_Assess potential fraud__ate_abort'
drbart_model_A = DRBART(parser_dir = '../../../models/'+model_name+'/concept-name/',
                     strict_parser=False)
evaluator_A = conduct_evaluation.ConductEvaluation(drbart_model_A, SampleOutcomes_DRBART_Normal_A, {
                                                        'activity_key' : 'concept:name',
                                                        'resource_key' : 'org:resource_start',
                                                    },
                                     test_event_log, n=N, n_processes=n_processes)
likelihoods_A = evaluator_A.sample_cases(False, True)

  0%|                                                                         | 0/6018 [00:00<?, ?it/s]

  0%|                                                              | 1/6018 [00:07<11:43:48,  7.02s/it]

  0%|                                                               | 2/6018 [00:09<7:45:13,  4.64s/it]

  0%|                                                               | 5/6018 [00:11<2:56:21,  1.76s/it]

  0%|                                                               | 6/6018 [00:13<3:06:04,  1.86s/it]

...

 98%|███████████████████████████████████████████████████████████▊ | 5901/6018 [00:21<00:00, 260.42it/s]

 99%|████████████████████████████████████████████████████████████ | 5928/6018 [00:21<00:00, 255.90it/s]

 99%|████████████████████████████████████████████████████████████▍| 5960/6018 [00:21<00:00, 259.67it/s]

100%|████████████████████████████████████████████████████████████▋| 5990/6018 [00:21<00:00, 266.07it/s]

100%|█████████████████████████████████████████████████████████████| 6018/6018 [00:21<00:00, 279.26it/s]

In [6]:
np.mean([v.ln() for v in likelihoods_A[0].values()])

Decimal('-70.67457287388107796766495753')

In [7]:
np.mean(get_pscores(likelihoods_A))

np.float64(2.413190513727962e+64)

In [8]:
drbart_model_R_A = DRBART(parser_dir = '../../../models/'+model_name+'/concept-name_resource/',
                     strict_parser=False)
evaluator_R_A = conduct_evaluation.ConductEvaluation(drbart_model_R_A, SampleOutcomes_DRBART_Normal_R_A,
                                                   {
                                                        'activity_key' : 'concept:name',
                                                        'resource_key' : 'org:resource_start',
                                                    },
                                     test_event_log, n=N, n_processes=n_processes)
likelihoods_R_A = evaluator_R_A.sample_cases(False, True)

FileNotFoundError: [Errno 2] No such file or directory: '../../../models/bpic_2017_all/concept-name_resource/ucuts.json'

In [9]:
np.mean([v.ln() for v in likelihoods_R_A[0].values()])

TypeError: 'NoneType' object is not subscriptable

In [10]:
np.mean(get_pscores(likelihoods_R_A))

TypeError: 'NoneType' object is not subscriptable

In [11]:
drbart_model_R = DRBART(parser_dir = '../../../models/'+model_name+'/resource/',
                     strict_parser=False)
evaluator_R = conduct_evaluation.ConductEvaluation(drbart_model_R, SampleOutcomes_DRBART_Normal_R,
                                                   {
                                                        'activity_key' : 'concept:name',
                                                        'resource_key' : 'org:resource_start',
                                                    },
                                     test_event_log, n=N, n_processes=n_processes)
likelihoods_R = evaluator_R.sample_cases(False, True)

FileNotFoundError: [Errno 2] No such file or directory: '../../../models/bpic_2017_all/resource/ucuts.json'

In [12]:
np.mean([v.ln() for v in likelihoods_R[0].values()])

TypeError: 'NoneType' object is not subscriptable

In [13]:
np.mean(get_pscores(likelihoods_R))

TypeError: 'NoneType' object is not subscriptable

In [14]:
drbart_model_R_A_S = DRBART(parser_dir = '../../../models/'+model_name+'/concept-name_resource_seconds-in-day/',
                     strict_parser=False)
evaluator_R_A_S = conduct_evaluation.ConductEvaluation(drbart_model_R_A_S, SampleOutcomes_DRBART_Normal_R_A_S,
                                                   {
                                                        'activity_key' : 'concept:name',
                                                        'resource_key' : 'org:resource_start',
                                                    },
                                     test_event_log, n=N, n_processes=n_processes)
likelihoods_R_A_S = evaluator_R_A_S.sample_cases(False, True)

  0%|                                                                         | 0/6018 [00:00<?, ?it/s]

  0%|                                                              | 1/6018 [00:21<35:31:15, 21.25s/it]

  0%|                                                              | 2/6018 [00:27<21:06:46, 12.63s/it]

  0%|                                                               | 7/6018 [00:28<4:20:49,  2.60s/it]

  0%|                                                              | 10/6018 [00:31<3:04:12,  1.84s/it]

...

 99%|████████████████████████████████████████████████████████████▎| 5951/6018 [00:28<00:00, 183.59it/s]

 99%|████████████████████████████████████████████████████████████▌| 5970/6018 [00:28<00:00, 184.29it/s]

100%|████████████████████████████████████████████████████████████▋| 5989/6018 [00:29<00:00, 179.65it/s]

100%|████████████████████████████████████████████████████████████▉| 6010/6018 [00:29<00:00, 185.86it/s]

100%|█████████████████████████████████████████████████████████████| 6018/6018 [00:29<00:00, 205.80it/s]

In [15]:
np.mean([v.ln() for v in likelihoods_R_A_S[0].values()])

Decimal('-20.43523397746553432141308988')

In [16]:
np.mean(get_pscores(likelihoods_R_A_S))

np.float64(5.807721965379444e+21)

In [17]:
drbart_model_R_A_S_AC = DRBART(parser_dir = '../../../models/'+model_name+'/concept-name_resource_seconds-in-day_activity-count/',
                     strict_parser=False)
evaluator_R_A_S_AC = conduct_evaluation.ConductEvaluation(drbart_model_R_A_S_AC, SampleOutcomes_DRBART_Normal_R_A_S_AC,
                                                   {
                                                        'activity_key' : 'concept:name',
                                                        'resource_key' : 'org:resource_start',
                                                        'known_activities' : known_activities,
                                                    },
                                     test_event_log, n=N, n_processes=n_processes)
likelihoods_R_A_S_AC = evaluator_R_A_S_AC.sample_cases(False, True)

  0%|                                                                         | 0/6018 [00:00<?, ?it/s]

  0%|                                                              | 1/6018 [00:40<67:37:34, 40.46s/it]

  0%|                                                              | 2/6018 [01:43<90:01:50, 53.87s/it]

  0%|                                                              | 3/6018 [01:44<49:31:04, 29.64s/it]

  1%|▍                                                             | 37/6018 [01:50<2:24:54,  1.45s/it]

...

 99%|████████████████████████████████████████████████████████████▎| 5955/6018 [00:36<00:00, 173.55it/s]

 99%|████████████████████████████████████████████████████████████▌| 5974/6018 [00:36<00:00, 165.72it/s]

100%|████████████████████████████████████████████████████████████▊| 5994/6018 [00:36<00:00, 165.23it/s]

100%|████████████████████████████████████████████████████████████▉| 6014/6018 [00:36<00:00, 160.29it/s]

100%|█████████████████████████████████████████████████████████████| 6018/6018 [00:36<00:00, 164.47it/s]

In [18]:
np.mean([v.ln() for v in likelihoods_R_A_S_AC[0].values()])

Decimal('-9.743375089231298123426096929')

In [19]:
np.mean(get_pscores(likelihoods_R_A_S_AC))

np.float64(89844893023011.86)

In [20]:
drbart_model_R_A_S_RC = DRBART(parser_dir = '../../../models/'+model_name+'/concept-name_resource_seconds-in-day_resource-count/',
                     strict_parser=False)
evaluator_R_A_S_RC = conduct_evaluation.ConductEvaluation(drbart_model_R_A_S_RC, SampleOutcomes_DRBART_Normal_R_A_S_RC,
                                                   {
                                                        'activity_key' : 'concept:name',
                                                        'resource_key' : 'org:resource_start',
                                                        'known_resources' : known_resources
                                                    },
                                     test_event_log, n=N, n_processes=n_processes)
likelihoods_R_A_S_RC = evaluator_R_A_S_RC.sample_cases(False, True)

  0%|                                                                         | 0/6018 [00:00<?, ?it/s]

  0%|                                                              | 1/6018 [00:14<25:01:25, 14.97s/it]

  0%|                                                              | 2/6018 [00:42<37:18:39, 22.33s/it]

  0%|▏                                                             | 15/6018 [00:44<3:21:23,  2.01s/it]

  0%|▏                                                             | 18/6018 [00:54<3:49:30,  2.30s/it]

...

 99%|████████████████████████████████████████████████████████████▎| 5952/6018 [00:38<00:00, 164.79it/s]

 99%|████████████████████████████████████████████████████████████▌| 5969/6018 [00:38<00:00, 164.34it/s]

 99%|████████████████████████████████████████████████████████████▋| 5986/6018 [00:38<00:00, 163.04it/s]

100%|████████████████████████████████████████████████████████████▊| 6003/6018 [00:38<00:00, 163.29it/s]

100%|█████████████████████████████████████████████████████████████| 6018/6018 [00:38<00:00, 154.77it/s]

In [21]:
np.mean([v.ln() for v in likelihoods_R_A_S_RC[0].values()])

Decimal('-5.445949313173493625311219575')

In [22]:
np.mean(get_pscores(likelihoods_R_A_S_RC))

np.float64(4315373.056608037)

In [23]:
drbart_model_R_A_S_RC_AC = DRBART(parser_dir = '../../../models/'+model_name+'/concept-name_resource_seconds-in-day_activity-count_resource_count/',
                     strict_parser=False)
evaluator_R_A_S_RC_AC = conduct_evaluation.ConductEvaluation(drbart_model_R_A_S_RC_AC, SampleOutcomes_DRBART_Normal_R_A_S_RC_AC,
                                                   {
                                                        'activity_key' : 'concept:name',
                                                        'resource_key' : 'org:resource_start',
                                                        'known_resources' : known_resources,
                                                        'known_activities' : known_activities,
                                                    },
                                     test_event_log, n=N, n_processes=n_processes)
likelihoods_R_A_S_RC_AC = evaluator_R_A_S_RC_AC.sample_cases(False, True)

  0%|                                                                         | 0/6018 [00:00<?, ?it/s]

  0%|                                                              | 1/6018 [00:46<77:19:35, 46.26s/it]

  0%|                                                             | 2/6018 [02:27<131:07:15, 78.46s/it]

  0%|▎                                                             | 30/6018 [03:24<8:35:59,  5.17s/it]

  1%|▌                                                             | 52/6018 [03:28<4:15:06,  2.57s/it]

...

 99%|████████████████████████████████████████████████████████████▍| 5961/6018 [00:35<00:00, 158.75it/s]

 99%|████████████████████████████████████████████████████████████▌| 5977/6018 [00:35<00:00, 144.03it/s]

100%|████████████████████████████████████████████████████████████▋| 5992/6018 [00:35<00:00, 142.40it/s]

100%|████████████████████████████████████████████████████████████▉| 6011/6018 [00:35<00:00, 154.61it/s]

100%|█████████████████████████████████████████████████████████████| 6018/6018 [00:35<00:00, 168.76it/s]

In [24]:
np.mean([v.ln() for v in likelihoods_R_A_S_RC_AC[0].values()])

Decimal('-Infinity')

In [25]:
np.mean(get_pscores(likelihoods_R_A_S_RC_AC))

np.float64(6.140986257667134e+16)

In [26]:
drbart_model_R_A_S_RC_AC_V = DRBART(parser_dir = '../../../models/'+model_name+'/concept-name_resource_seconds-in-day_activity-count_resource_count_amount/',
                     strict_parser=False)
evaluator_R_A_S_RC_AC_V = conduct_evaluation.ConductEvaluation(drbart_model_R_A_S_RC_AC_V, SampleOutcomes_DRBART_Normal_R_A_S_RC_AC_V,
                                                   {
                                                        'activity_key' : 'concept:name',
                                                        'resource_key' : 'org:resource_start',
                                                        'value_key' : 'case:RequestedAmount_start',
                                                        'known_resources' : known_resources,
                                                        'known_activities' : known_activities,
                                                    },
                                     test_event_log, n=N, n_processes=n_processes)
likelihoods_R_A_S_RC_AC_V = evaluator_R_A_S_RC_AC_V.sample_cases(False, False)

  0%|                                                                         | 0/6018 [00:00<?, ?it/s]

  0%|                                                              | 1/6018 [00:47<78:54:58, 47.22s/it]

  0%|                                                             | 2/6018 [02:39<142:24:58, 85.22s/it]

  0%|                                                             | 3/6018 [03:12<102:59:00, 61.64s/it]

  0%|                                                              | 4/6018 [03:33<76:14:00, 45.63s/it]

...

100%|██████████████████████████████████████████████████████████▉| 6015/6018 [29:48:16<00:14,  4.72s/it]

100%|██████████████████████████████████████████████████████████▉| 6016/6018 [29:48:23<00:10,  5.29s/it]

100%|██████████████████████████████████████████████████████████▉| 6017/6018 [29:48:25<00:04,  4.45s/it]

100%|███████████████████████████████████████████████████████████| 6018/6018 [29:48:27<00:00,  3.47s/it]

100%|███████████████████████████████████████████████████████████| 6018/6018 [29:48:27<00:00, 17.83s/it]

In [27]:
np.mean([v.ln() for v in likelihoods_R_A_S_RC_AC_V[0].values()])

Decimal('-Infinity')

In [28]:
np.mean(get_pscores(likelihoods_R_A_S_RC_AC_V))

np.float64(12473535280.506405)

In [29]:
drbart_model_R_A_S_D = DRBART(parser_dir = '../../../models/'+model_name+'/concept-name_resource_seconds-in-day_day-of-week/',
                     strict_parser=False)
evaluator_R_A_S_D = conduct_evaluation.ConductEvaluation(drbart_model_R_A_S_D, SampleOutcomes_DRBART_Normal_R_A_S_D,
                                                   {
                                                        'activity_key' : 'concept:name',
                                                        'resource_key' : 'org:resource_start',
                                                    },
                                     test_event_log, n=N, n_processes=n_processes)
likelihoods_R_A_S_D = evaluator_R_A_S_D.sample_cases(False, True)

  0%|                                                                                                                                                                                        | 0/6018 [00:00<?, ?it/s]

  0%|                                                                                                                                                                             | 1/6018 [00:24<41:10:00, 24.63s/it]

  0%|                                                                                                                                                                             | 2/6018 [00:39<31:09:34, 18.65s/it]

  0%|▏                                                                                                                                                                             | 7/6018 [00:44<7:28:36,  4.48s/it]

  0%|▍                                                                                                                                                                            | 15/6018 [00:57<4:21:31,  2.61s/it]

...

 99%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████  | 5952/6018 [00:27<00:00, 195.91it/s]

 99%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▋ | 5972/6018 [00:27<00:00, 196.87it/s]

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▎| 5996/6018 [00:28<00:00, 188.65it/s]

100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 6018/6018 [00:28<00:00, 191.75it/s]

100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 6018/6018 [00:28<00:00, 213.70it/s]

In [30]:
np.mean([v.ln() for v in likelihoods_R_A_S_D[0].values()])

Decimal('-16.16600935047215999851629272')

In [31]:
np.mean(get_pscores(likelihoods_R_A_S_D))

np.float64(1.8882849373045473e+19)

In [32]:
drbart_model_R_A_S_D_RC_AC = DRBART(parser_dir = '../../../models/'+model_name+'/concept-name_resource_seconds-in-day_day-of-week_activity-count_resoure-count/',
                     strict_parser=False)
evaluator_R_A_S_D_RC_AC = conduct_evaluation.ConductEvaluation(drbart_model_R_A_S_D_RC_AC, SampleOutcomes_DRBART_Normal_R_A_S_D_RC_AC,
                                                   {
                                                        'activity_key' : 'concept:name',
                                                        'resource_key' : 'org:resource_start',
                                                        'known_resources' : known_resources,
                                                        'known_activities' : known_activities,
                                                    },
                                     test_event_log, n=N, n_processes=n_processes)
likelihoods_R_A_S_D_RC_AC = evaluator_R_A_S_D_RC_AC.sample_cases(False, True)

  0%|                                                                                                                                                                                        | 0/6018 [00:00<?, ?it/s]

  0%|                                                                                                                                                                             | 1/6018 [00:17<28:37:22, 17.13s/it]

  0%|                                                                                                                                                                             | 2/6018 [00:58<52:30:57, 31.43s/it]

  0%|▌                                                                                                                                                                            | 21/6018 [01:06<3:42:33,  2.23s/it]

  0%|▋                                                                                                                                                                            | 22/6018 [01:16<4:35:36,  2.76s/it]

...

  5%|███████▉                                                                                                                                                                    | 279/6018 [07:07<1:50:20,  1.15s/it]

  5%|████████                                                                                                                                                                    | 280/6018 [07:08<1:47:30,  1.12s/it]

  5%|████████                                                                                                                                                                    | 281/6018 [07:08<1:43:08,  1.08s/it]

  5%|████████                                                                                                                                                                    | 281/6018 [07:08<2:25:50,  1.53s/it]

KeyError: 13

In [33]:
np.mean([v.ln() for v in likelihoods_R_A_S_D_RC_AC[0].values()])

TypeError: 'NoneType' object is not subscriptable

In [34]:
np.mean(get_pscores(likelihoods_R_A_S_D_RC_AC))

TypeError: 'NoneType' object is not subscriptable

In [35]:
results = {
    'drbart_model_A' : likelihoods_A,
    'drbart_model_R' : likelihoods_R,
    'drbart_model_R_A' : likelihoods_R_A,
    'drbart_model_R_A_S' : likelihoods_R_A_S,
    'drbart_model_R_A_S_AC' : likelihoods_R_A_S_AC,
    'drbart_model_R_A_S_RC' : likelihoods_R_A_S_RC,
    'drbart_model_R_A_S_RC_AC' : likelihoods_R_A_S_RC_AC,
    'drbart_model_R_A_S_RC_AC_V' : likelihoods_R_A_S_RC_AC_V,
    'drbart_model_R_A_S_D' : likelihoods_R_A_S_D,
    'drbart_model_R_A_S_D_RC_AC' : likelihoods_R_A_S_D_RC_AC
}
with open('./'+model_name+'_dr_bart_evaluation_'+log_name+'.pickle', 'wb') as handle:
    pickle.dump(results, handle)